In [1]:
# --------------------

# --------------------
#!pip install pyspark

In [2]:
# Import necessary libraries
import os
from pyspark.sql import SparkSession
from pyspark.sql.functions import split, col
from pyspark.sql.types import StructType, StructField, StringType, IntegerType


from pyspark.ml.feature import StringIndexer, VectorAssembler
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml import Pipeline


In [3]:
# Step 1: Create Spark Session
spark = SparkSession.builder \
    .appName("MTA_Turnstile_Streaming") \
    .config("spark.jars.packages", 
            "org.apache.spark:spark-sql-kafka-0-10_2.12:3.5.0," \
            "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
    .config("spark.sql.shuffle.partitions", "2") \
    .getOrCreate()

spark.sparkContext.setLogLevel("INFO")


:: loading settings :: url = jar:file:/opt/anaconda3/lib/python3.11/site-packages/pyspark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /Users/gopalakrishnaabba/.ivy2/cache
The jars for the packages stored in: /Users/gopalakrishnaabba/.ivy2/jars
org.apache.spark#spark-sql-kafka-0-10_2.12 added as a dependency
org.mongodb.spark#mongo-spark-connector_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-a2b216d7-c20c-4076-9f84-e1d0b639adc3;1.0
	confs: [default]
	found org.apache.spark#spark-sql-kafka-0-10_2.12;3.5.0 in central
	found org.apache.spark#spark-token-provider-kafka-0-10_2.12;3.5.0 in central
	found org.apache.kafka#kafka-clients;3.4.1 in central
	found org.lz4#lz4-java;1.8.0 in central
	found org.xerial.snappy#snappy-java;1.1.10.3 in central
	found org.slf4j#slf4j-api;2.0.7 in central
	found org.apache.hadoop#hadoop-client-runtime;3.3.4 in central
	found org.apache.hadoop#hadoop-client-api;3.3.4 in central
	found commons-logging#commons-logging;1.1.3 in central
	found com.google.code.findbugs#jsr305;3.0.0 in central
	found org.apache.commons#com

In [4]:
# Step 2: Define schema of MTA turnstile data
turnstile_schema = StructType([
    StructField("C/A", StringType(), True),
    StructField("UNIT", StringType(), True),
    StructField("SCP", StringType(), True),
    StructField("STATION", StringType(), True),
    StructField("LINENAME", StringType(), True),
    StructField("DIVISION", StringType(), True),
    StructField("DATE", StringType(), True),
    StructField("TIME", StringType(), True),
    StructField("DESC", StringType(), True),
    StructField("ENTRIES", IntegerType(), True),
    StructField("EXITS", IntegerType(), True)
])

In [5]:
# Step 3: Read data from Kafka
kafka_df = spark.readStream \
    .format("kafka") \
    .option("kafka.bootstrap.servers", "localhost:9092") \
    .option("subscribe", "mta_turnstile_topic") \
    .option("startingOffsets", "latest") \
    .load()

25/05/04 17:17:12 INFO SharedState: Setting hive.metastore.warehouse.dir ('null') to the value of spark.sql.warehouse.dir.
25/05/04 17:17:12 INFO SharedState: Warehouse path is 'file:/Users/gopalakrishnaabba/spark-warehouse'.


In [6]:
# Step 4: Parse the Kafka 'value' as CSV
turnstile_values = kafka_df.selectExpr("CAST(value AS STRING) as csv")
split_col = split(turnstile_values['csv'], ',')

In [7]:
# Step 5: Extract structured columns
turnstile_df = turnstile_values.select(
    split_col.getItem(0).alias("C/A"),
    split_col.getItem(1).alias("UNIT"),
    split_col.getItem(2).alias("SCP"),
    split_col.getItem(3).alias("STATION"),
    split_col.getItem(4).alias("LINENAME"),
    split_col.getItem(5).alias("DIVISION"),
    split_col.getItem(6).alias("DATE"),
    split_col.getItem(7).alias("TIME"),
    split_col.getItem(8).alias("DESC"),
    split_col.getItem(9).cast("integer").alias("ENTRIES"),
    split_col.getItem(10).cast("integer").alias("EXITS")
)

In [8]:
# Step 6: Aggregate live entry/exit counts by STATION
aggregated_df = turnstile_df.groupBy("STATION").sum("ENTRIES", "EXITS")

In [9]:
# # Step 7: Output to memory (for model training) and console (for monitoring)
# query_console = aggregated_df.writeStream \
#     .outputMode("complete") \
#     .format("console") \
#     .option("truncate", False) \
#     .start()

# query_memory = aggregated_df.writeStream \
#     .outputMode("complete") \
#     .format("memory") \
#     .queryName("aggregated_turnstile") \
#     .start()


# query_console.awaitTermination()
# query_memory.awaitTermination()




In [10]:
# Step 7: Output to memory (for training), console (monitoring), and MongoDB (storage)

# 1. Console Sink – for live monitoring
query_console = aggregated_df.writeStream \
    .outputMode("complete") \
    .format("console") \
    .option("truncate", False) \
    .start()

# 2. MongoDB Sink – via foreachBatch
def write_to_mongo(batch_df, batch_id):
    batch_df.write \
        .format("mongo") \
        .option("uri", "mongodb://localhost:27017/mta_db.foot_traffic") \
        .mode("overwrite") \
        .save()

query_mongo = aggregated_df.writeStream \
    .outputMode("complete") \
    .foreachBatch(write_to_mongo) \
    .start()

# 3. Optional Memory Sink – if you still want to query from memory (for model training)
query_memory = aggregated_df.writeStream \
    .outputMode("complete") \
    .format("memory") \
    .queryName("aggregated_turnstile") \
    .start()

# Wait for all queries
query_console.awaitTermination()
query_mongo.awaitTermination()
query_memory.awaitTermination()


25/05/04 17:17:13 INFO StateStoreCoordinatorRef: Registered StateStoreCoordinator endpoint
25/05/04 17:17:13 WARN ResolveWriteToStream: Temporary checkpoint location created which is deleted normally when the query didn't fail: /private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-b994e04a-109a-4e61-8838-9126805e0f01. If it's required to delete it under any circumstances, please set spark.sql.streaming.forceDeleteTempCheckpointLocation to true. Important to know deleting temp checkpoint folder is best effort.
25/05/04 17:17:13 INFO ResolveWriteToStream: Checkpoint root file:///private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-b994e04a-109a-4e61-8838-9126805e0f01 resolved to file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-b994e04a-109a-4e61-8838-9126805e0f01.
25/05/04 17:17:13 WARN ResolveWriteToStream: spark.sql.adaptive.enabled is not supported in streaming DataFrames/Datasets and will be disabled.
25/05/04 17:17:13 INFO CheckpointF

-------------------------------------------
Batch: 0
-------------------------------------------
+-------+------------+----------+
|STATION|sum(ENTRIES)|sum(EXITS)|
+-------+------------+----------+
+-------+------------+----------+



25/05/04 17:17:16 INFO CodeGenerator: Code generated in 9.897625 ms (0 + 2) / 2]
25/05/04 17:17:16 INFO Executor: Finished task 1.0 in stage 5.0 (TID 5). 7375 bytes result sent to driver
25/05/04 17:17:16 INFO Executor: Finished task 0.0 in stage 5.0 (TID 4). 7375 bytes result sent to driver
25/05/04 17:17:16 INFO TaskSetManager: Finished task 0.0 in stage 5.0 (TID 4) in 858 ms on gopalas-laptop.lan (executor driver) (1/2)
25/05/04 17:17:16 INFO TaskSetManager: Finished task 1.0 in stage 5.0 (TID 5) in 857 ms on gopalas-laptop.lan (executor driver) (2/2)
25/05/04 17:17:16 INFO TaskSchedulerImpl: Removed TaskSet 5.0, whose tasks have all completed, from pool 
25/05/04 17:17:16 INFO DAGScheduler: ResultStage 5 (start at NativeMethodAccessorImpl.java:0) finished in 0.882 s
25/05/04 17:17:16 INFO DAGScheduler: Job 2 is finished. Cancelling potential speculative or zombie tasks for this job
25/05/04 17:17:16 INFO TaskSchedulerImpl: Killing all running tasks in stage 5: Stage finished
25/05/

-------------------------------------------
Batch: 1
-------------------------------------------
+---------------+------------+----------+
|STATION        |sum(ENTRIES)|sum(EXITS)|
+---------------+------------+----------+
|WORLD TRADE CTR|3180        |14909     |
+---------------+------------+----------+

CodeCache: size=131072Kb used=34701Kb max_used=34715Kb free=96370Kb
 bounds [0x0000000102e14000, 0x0000000105024000, 0x000000010ae14000]
 total_blobs=13317 nmethods=12220 adapters=1011
 compilation: disabled (not enough contiguous free space left)


25/05/04 17:17:24 INFO CheckpointFileManager: Writing atomically to file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-d18688dd-ceee-4bc8-ab55-0dc8cc46c808/offsets/2 using temp file file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-d18688dd-ceee-4bc8-ab55-0dc8cc46c808/offsets/.2.897c5379-1794-49a2-ae79-419aff42b1ab.tmp
25/05/04 17:17:24 INFO CheckpointFileManager: Writing atomically to file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-b994e04a-109a-4e61-8838-9126805e0f01/offsets/2 using temp file file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-b994e04a-109a-4e61-8838-9126805e0f01/offsets/.2.194013a0-e174-42be-9b88-d860a8c39c46.tmp
25/05/04 17:17:24 INFO CheckpointFileManager: Writing atomically to file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/temporary-46995783-99a5-40d1-bb26-f30c4e147b64/offsets/2 using temp file file:/private/var/folders/48/hk2s0t4x1xv5gpns58fpsx1m0000gn/T/tempora

...

-------------------------------------------
Batch: 64
-------------------------------------------
+---------------+------------+----------+
|STATION        |sum(ENTRIES)|sum(EXITS)|
+---------------+------------+----------+
|WORLD TRADE CTR|30019       |177420    |
|FULTON ST      |6504        |40328     |
|34 ST-HERALD SQ|15498       |94098     |
|125 ST         |5448        |26978     |
|23 ST          |8222        |35867     |
|34 ST-PENN STA |14421       |88278     |
|161/YANKEE STAD|16847       |120622    |
|CANAL ST       |2730        |17765     |
|42 ST-PORT AUTH|4881        |18183     |
|TIME SQ-42 ST  |25520       |183052    |
+---------------+------------+----------+



25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_830_piece0 on gopalas-laptop.lan:65359 in memory (size: 36.9 KiB, free: 361.6 MiB)
25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_832_piece0 on gopalas-laptop.lan:65359 in memory (size: 36.9 KiB, free: 361.7 MiB)
25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_831_piece0 on gopalas-laptop.lan:65359 in memory (size: 36.9 KiB, free: 361.7 MiB)
25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_838_piece0 on gopalas-laptop.lan:65359 in memory (size: 34.3 KiB, free: 361.8 MiB)
25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_841_piece0 on gopalas-laptop.lan:65359 in memory (size: 413.0 B, free: 361.8 MiB)
25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_833_piece0 on gopalas-laptop.lan:65359 in memory (size: 36.9 KiB, free: 361.8 MiB)
25/05/04 17:24:49 INFO BlockManagerInfo: Removed broadcast_839_piece0 on gopalas-laptop.lan:65359 in memory (size: 34.2 KiB, free: 361.8 MiB)
25/05/0

-------------------------------------------
Batch: 65
-------------------------------------------
+---------------+------------+----------+
|STATION        |sum(ENTRIES)|sum(EXITS)|
+---------------+------------+----------+
|WORLD TRADE CTR|30019       |177420    |
|FULTON ST      |6504        |40328     |
|34 ST-HERALD SQ|18050       |110683    |
|125 ST         |5448        |26978     |
|23 ST          |8222        |35867     |
|34 ST-PENN STA |14421       |88278     |
|161/YANKEE STAD|16847       |120622    |
|CANAL ST       |2730        |17765     |
|42 ST-PORT AUTH|4881        |18183     |
|TIME SQ-42 ST  |25520       |183052    |
+---------------+------------+----------+



25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_845_piece0 on gopalas-laptop.lan:65359 in memory (size: 36.9 KiB, free: 361.5 MiB)
25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_850_piece0 on gopalas-laptop.lan:65359 in memory (size: 20.3 KiB, free: 361.5 MiB)
25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_852_piece0 on gopalas-laptop.lan:65359 in memory (size: 34.2 KiB, free: 361.6 MiB)
25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_854_piece0 on gopalas-laptop.lan:65359 in memory (size: 413.0 B, free: 361.6 MiB)
25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_853_piece0 on gopalas-laptop.lan:65359 in memory (size: 40.0 KiB, free: 361.6 MiB)
25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_843_piece0 on gopalas-laptop.lan:65359 in memory (size: 36.9 KiB, free: 361.6 MiB)
25/05/04 17:24:51 INFO BlockManagerInfo: Removed broadcast_848_piece0 on gopalas-laptop.lan:65359 in memory (size: 20.3 KiB, free: 361.7 MiB)
25/05/0

KeyboardInterrupt: 